# 1. 필요한 모듈 불러오기

In [1]:
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.metrics import *
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from xgboost import XGBClassifier
import pandas as pd
import numpy as np
import torch

# 2. 파일 불러오기

In [2]:
data = pd.read_csv('labels_included.csv')
data

rank_popularity       webtoon_name  rating  \
0                89.0               노블레스    9.62   
1                48.0          갓 오브 하이스쿨    9.64   
2                28.0            유미의 세포들    9.93   
3               270.0               여신강림    9.34   
4               429.0               싸움독학    9.67   
...               ...                ...     ...   
1202              NaN         노래 못 하는 남자    9.92   
1203              NaN  마섹남 - 마술하는 섹시한 남자    9.89   
1204              NaN       주인공의 주식을 팝니다    9.84   
1205              NaN              프린키피아    9.84   
1206              NaN              프린키피아    9.84   

                                                   link genre  interest  \
0     https://comic.naver.com/webtoon/list?titleId=2...   판타지   1371554   
1     https://comic.naver.com/webtoon/list?titleId=3...   판타지   1371113   
2     https://comic.naver.com/webtoon/list?titleId=6...   로맨스   1285627   
3     https://comic.naver.com/webtoon/list?titleId=7...   로맨스   1216760   
4     https://comic.naver.com/webtoon/list?titleId=7...    액션   1115468   
...                                                 ...   ...       ...   
1202  https://comic.naver.com/webtoon/list?titleId=8...   로맨스     22545   
1203  https://comic.naver.com/webtoon/list?titleId=7...   로맨스     54426   
1204  https://comic.naver.com/webtoon/list?titleId=8...   로맨스     57199   
1205  https://comic.naver.com/webtoon/list?titleId=8...   판타지     23203   
1206  https://comic.naver.com/webtoon/list?titleId=8...   판타지     23203   

      episode_count  originality               authors  work_count  ...   행복  \
0               545            0        ['손제호', '이광수']    3.500000  ...  0.0   
1               573            0               ['박용제']    2.000000  ...  0.0   
2               512            0               ['이동건']   11.000000  ...  0.0   
3               261            0               ['야옹이']    4.000000  ...  0.0   
4               223            0        ['박만사', '김정현']   13.500000  ...  0.0   
...             ...          ...                   ...         ...  ...  ...   
1202             57            0         ['재은', '이해금']    1.000000  ...  0.0   
1203             90            1  ['랑또', '육시몬', '티르스']    4.000000  ...  0.0   
1204             96            1   ['목감기', '가얌', '50']    1.333333  ...  0.0   
1205             66            0         ['버튼', '한경찰']    3.500000  ...  0.0   
1206             66            0         ['버튼', '한경찰']    3.500000  ...  0.0   

         화남/분노     환영/호의  흐뭇함(귀여움/예쁨)  힘듦/지침  day  rank_day  scaled_interest  \
0     0.000000  0.000000     0.000000    0.0  NaN       NaN      9198.671890   
1     0.000000  0.000000     0.013333    0.0  NaN       NaN      9195.681202   
2     0.066667  0.013333     0.026667    0.0  NaN       NaN      8615.948845   
3     0.000000  0.000000     0.053333    0.0  NaN       NaN      8148.919995   
4     0.013333  0.000000     0.013333    0.0  NaN       NaN      7461.997576   
...        ...       ...          ...    ...  ...       ...              ...   
1202  0.032258  0.000000     0.064516    0.0  sun      92.0        50.224573   
1203  0.014493  0.014493     0.028986    0.0  sun      93.0       266.428949   
1204  0.017857  0.000000     0.071429    0.0  sun      94.0       285.234342   
1205  0.000000  0.000000     0.045455    0.0  sun      95.0        54.686870   
1206  0.000000  0.000000     0.045455    0.0  sun      95.0        54.686870   

      scaled_rank  cluster  
0      961.736887      7.0  
1      979.363715      7.0  
2      987.962167      7.0  
3      883.920894      7.0  
4      815.563199      7.0  
...           ...      ...  
1202    30.303030      0.0  
1203    23.088023      0.0  
1204    12.987013      0.0  
1205   141.444540      0.0  
1206     2.886003      0.0  

[1207 rows x 56 columns]

# 3. EDA

In [3]:
data.isna().sum()

rank_popularity        548
webtoon_name             0
rating                   0
link                     0
genre                    0
interest                 0
episode_count            0
originality              0
authors                  0
work_count               0
previous_work            0
likes                    0
rating_participants      0
comments_count           0
감동/감탄                    0
경악                       0
고마움                      0
공포/무서움                   0
귀찮음                      0
기대감                      0
기쁨                       0
깨달음                      0
놀람                       0
당황/난처                    0
부담/안_내킴                  0
불쌍함/연민                   0
불안/걱정                    0
불평/불만                    0
비장함                      0
슬픔                       0
신기함/관심                   0
아껴주는                     0
안심/신뢰                    0
안타까움/실망                  0
어이없음                     0
없음                       0
우쭐댐/무시함                  0
의

In [4]:
data.drop(['rank_popularity', 'day', 'rank_day'], axis = 1, inplace = True)

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1207 entries, 0 to 1206
Data columns (total 53 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   webtoon_name         1207 non-null   object 
 1   rating               1207 non-null   float64
 2   link                 1207 non-null   object 
 3   genre                1207 non-null   object 
 4   interest             1207 non-null   int64  
 5   episode_count        1207 non-null   int64  
 6   originality          1207 non-null   int64  
 7   authors              1207 non-null   object 
 8   work_count           1207 non-null   float64
 9   previous_work        1207 non-null   float64
 10  likes                1207 non-null   int64  
 11  rating_participants  1207 non-null   int64  
 12  comments_count       1207 non-null   int64  
 13  감동/감탄                1207 non-null   float64
 14  경악                   1207 non-null   float64
 15  고마움                  1207 non-null   f

In [6]:
data.describe()

rating      interest  episode_count  originality   work_count  \
count  1207.000000  1.207000e+03    1207.000000  1207.000000  1207.000000   
mean      9.852742  2.030039e+05     116.200497     0.236951     3.560411   
std       0.333871  1.884953e+05     115.975606     0.425388     7.361153   
min       3.810000  1.515400e+04      21.000000     0.000000     1.000000   
25%       9.870000  9.877250e+04      56.000000     0.000000     1.000000   
50%       9.940000  1.426810e+05      88.000000     0.000000     2.000000   
75%       9.960000  2.513915e+05     136.000000     0.000000     3.500000   
max       9.980000  1.489716e+06    1414.000000     1.000000    95.000000   

       previous_work          likes  rating_participants  comments_count  \
count    1207.000000    1207.000000          1207.000000     1207.000000   
mean        0.498757   70375.140017         91540.247722    10940.802817   
std         0.500206   64891.541399         89606.904846    17265.927958   
min         0.000000    2602.000000          3155.000000      208.000000   
25%         0.000000   21287.000000         24231.500000     1510.500000   
50%         0.000000   50938.000000         59360.000000     4055.000000   
75%         1.000000   98807.000000        133011.000000    13121.500000   
max         1.000000  442694.000000        696127.000000   190746.000000   

             감동/감탄  ...           짜증          한심함           행복        화남/분노  \
count  1207.000000  ...  1207.000000  1207.000000  1207.000000  1207.000000   
mean      0.136053  ...     0.030617     0.014965     0.001694     0.016397   
std       0.088495  ...     0.033388     0.019160     0.005839     0.024739   
min       0.000000  ...     0.000000     0.000000     0.000000     0.000000   
25%       0.078536  ...     0.000000     0.000000     0.000000     0.000000   
50%       0.120000  ...     0.026667     0.013333     0.000000     0.013333   
75%       0.174802  ...     0.040270     0.026667     0.000000     0.026667   
max       0.613333  ...     0.240000     0.150685     0.044444     0.200000   

             환영/호의  흐뭇함(귀여움/예쁨)        힘듦/지침  scaled_interest   scaled_rank  \
count  1207.000000  1207.000000  1207.000000      1207.000000  1.207000e+03   
mean      0.003977     0.030312     0.001580      1274.032293  5.867348e+02   
std       0.008736     0.041499     0.005288      1278.295886  2.575755e+02   
min       0.000000     0.000000     0.000000         0.101724  1.110223e-13   
25%       0.000000     0.000000     0.000000       567.169432  4.078914e+02   
50%       0.000000     0.014493     0.000000       864.939573  6.147186e+02   
75%       0.000000     0.040541     0.000000      1602.171335  7.952253e+02   
max       0.071429     0.288889     0.053333     10000.000000  1.000000e+03   

           cluster  
count  1207.000000  
mean      3.150787  
std       1.943769  
min       0.000000  
25%       2.000000  
50%       3.000000  
75%       4.000000  
max       7.000000  

[8 rows x 49 columns]

In [7]:
data.groupby('cluster')['genre'].value_counts()

cluster  genre
0.0      로맨스      53
         판타지      38
         드라마      33
         액션       14
         스릴러      11
                  ..
7.0      개그        4
         스릴러       3
         스포츠       2
         무협/사극     2
         일상        1
Name: count, Length: 77, dtype: int64

# 4. 모델 학습

In [8]:
# GPU 사용설정 확인
print("PyTorch version:", torch.__version__)
print("CUDA available:", torch.cuda.is_available())
print("CUDA version:", torch.version.cuda)
print("Device count:", torch.cuda.device_count())
if torch.cuda.is_available():
    print("Current GPU:", torch.cuda.get_device_name(0))

PyTorch version: 2.5.1+cu124
CUDA available: True
CUDA version: 12.4
Device count: 2
Current GPU: NVIDIA GeForce RTX 4090


In [9]:
# PyTorch에서 GPU 설정 확인
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using device: {device}")

Using device: cuda


In [10]:
data

webtoon_name  rating  \
0                  노블레스    9.62   
1             갓 오브 하이스쿨    9.64   
2               유미의 세포들    9.93   
3                  여신강림    9.34   
4                  싸움독학    9.67   
...                 ...     ...   
1202         노래 못 하는 남자    9.92   
1203  마섹남 - 마술하는 섹시한 남자    9.89   
1204       주인공의 주식을 팝니다    9.84   
1205              프린키피아    9.84   
1206              프린키피아    9.84   

                                                   link genre  interest  \
0     https://comic.naver.com/webtoon/list?titleId=2...   판타지   1371554   
1     https://comic.naver.com/webtoon/list?titleId=3...   판타지   1371113   
2     https://comic.naver.com/webtoon/list?titleId=6...   로맨스   1285627   
3     https://comic.naver.com/webtoon/list?titleId=7...   로맨스   1216760   
4     https://comic.naver.com/webtoon/list?titleId=7...    액션   1115468   
...                                                 ...   ...       ...   
1202  https://comic.naver.com/webtoon/list?titleId=8...   로맨스     22545   
1203  https://comic.naver.com/webtoon/list?titleId=7...   로맨스     54426   
1204  https://comic.naver.com/webtoon/list?titleId=8...   로맨스     57199   
1205  https://comic.naver.com/webtoon/list?titleId=8...   판타지     23203   
1206  https://comic.naver.com/webtoon/list?titleId=8...   판타지     23203   

      episode_count  originality               authors  work_count  \
0               545            0        ['손제호', '이광수']    3.500000   
1               573            0               ['박용제']    2.000000   
2               512            0               ['이동건']   11.000000   
3               261            0               ['야옹이']    4.000000   
4               223            0        ['박만사', '김정현']   13.500000   
...             ...          ...                   ...         ...   
1202             57            0         ['재은', '이해금']    1.000000   
1203             90            1  ['랑또', '육시몬', '티르스']    4.000000   
1204             96            1   ['목감기', '가얌', '50']    1.333333   
1205             66            0         ['버튼', '한경찰']    3.500000   
1206             66            0         ['버튼', '한경찰']    3.500000   

      previous_work  ...        짜증       한심함   행복     화남/분노     환영/호의  \
0               0.0  ...  0.026667  0.000000  0.0  0.000000  0.000000   
1               1.0  ...  0.000000  0.013333  0.0  0.000000  0.000000   
2               1.0  ...  0.106667  0.026667  0.0  0.066667  0.013333   
3               0.0  ...  0.066667  0.040000  0.0  0.000000  0.000000   
4               1.0  ...  0.000000  0.000000  0.0  0.013333  0.000000   
...             ...  ...       ...       ...  ...       ...       ...   
1202            0.0  ...  0.032258  0.000000  0.0  0.032258  0.000000   
1203            1.0  ...  0.014493  0.000000  0.0  0.014493  0.014493   
1204            1.0  ...  0.000000  0.000000  0.0  0.017857  0.000000   
1205            1.0  ...  0.030303  0.015152  0.0  0.000000  0.000000   
1206            1.0  ...  0.030303  0.015152  0.0  0.000000  0.000000   

      흐뭇함(귀여움/예쁨)  힘듦/지침  scaled_interest  scaled_rank  cluster  
0        0.000000    0.0      9198.671890   961.736887      7.0  
1        0.013333    0.0      9195.681202   979.363715      7.0  
2        0.026667    0.0      8615.948845   987.962167      7.0  
3        0.053333    0.0      8148.919995   883.920894      7.0  
4        0.013333    0.0      7461.997576   815.563199      7.0  
...           ...    ...              ...          ...      ...  
1202     0.064516    0.0        50.224573    30.303030      0.0  
1203     0.028986    0.0       266.428949    23.088023      0.0  
1204     0.071429    0.0       285.234342    12.987013      0.0  
1205     0.045455    0.0        54.686870   141.444540      0.0  
1206     0.045455    0.0        54.686870     2.886003      0.0  

[1207 rows x 53 columns]

In [11]:
data_cleaned = data.drop(['webtoon_name', 'link', 'authors', 'scaled_rank', 'scaled_interest'], axis = 1)
data_cleaned

rating genre  interest  episode_count  originality  work_count  \
0       9.62   판타지   1371554            545            0    3.500000   
1       9.64   판타지   1371113            573            0    2.000000   
2       9.93   로맨스   1285627            512            0   11.000000   
3       9.34   로맨스   1216760            261            0    4.000000   
4       9.67    액션   1115468            223            0   13.500000   
...      ...   ...       ...            ...          ...         ...   
1202    9.92   로맨스     22545             57            0    1.000000   
1203    9.89   로맨스     54426             90            1    4.000000   
1204    9.84   로맨스     57199             96            1    1.333333   
1205    9.84   판타지     23203             66            0    3.500000   
1206    9.84   판타지     23203             66            0    3.500000   

      previous_work   likes  rating_participants  comments_count  ...  \
0               0.0   91983               263859           82093  ...   
1               1.0  134823               261048           56406  ...   
2               1.0  355753               211459           32296  ...   
3               0.0  373202               356731           41199  ...   
4               1.0  265394               197599           17442  ...   
...             ...     ...                  ...             ...  ...   
1202            0.0    4658                 3955             282  ...   
1203            1.0   21651                17845            1257  ...   
1204            1.0   27970                21482            1275  ...   
1205            1.0    9460                 9436             680  ...   
1206            1.0    9460                 9436             680  ...   

         증오/혐오  지긋지긋        짜증       한심함   행복     화남/분노     환영/호의  \
0     0.000000   0.0  0.026667  0.000000  0.0  0.000000  0.000000   
1     0.000000   0.0  0.000000  0.013333  0.0  0.000000  0.000000   
2     0.000000   0.0  0.106667  0.026667  0.0  0.066667  0.013333   
3     0.000000   0.0  0.066667  0.040000  0.0  0.000000  0.000000   
4     0.013333   0.0  0.000000  0.000000  0.0  0.013333  0.000000   
...        ...   ...       ...       ...  ...       ...       ...   
1202  0.000000   0.0  0.032258  0.000000  0.0  0.032258  0.000000   
1203  0.000000   0.0  0.014493  0.000000  0.0  0.014493  0.014493   
1204  0.000000   0.0  0.000000  0.000000  0.0  0.017857  0.000000   
1205  0.000000   0.0  0.030303  0.015152  0.0  0.000000  0.000000   
1206  0.000000   0.0  0.030303  0.015152  0.0  0.000000  0.000000   

      흐뭇함(귀여움/예쁨)  힘듦/지침  cluster  
0        0.000000    0.0      7.0  
1        0.013333    0.0      7.0  
2        0.026667    0.0      7.0  
3        0.053333    0.0      7.0  
4        0.013333    0.0      7.0  
...           ...    ...      ...  
1202     0.064516    0.0      0.0  
1203     0.028986    0.0      0.0  
1204     0.071429    0.0      0.0  
1205     0.045455    0.0      0.0  
1206     0.045455    0.0      0.0  

[1207 rows x 48 columns]

In [12]:
# 'genre' 열을 원핫인코딩
genre_dummies = pd.get_dummies(data_cleaned['genre'], prefix='genre')

# 기존 데이터프레임에 원핫인코딩 결과 추가
data_cleaned = pd.concat([data_cleaned, genre_dummies], axis=1)
data_cleaned.drop('genre', axis = 1, inplace=True)

data_cleaned.head()

rating  interest  episode_count  originality  work_count  previous_work  \
0    9.62   1371554            545            0         3.5            0.0   
1    9.64   1371113            573            0         2.0            1.0   
2    9.93   1285627            512            0        11.0            1.0   
3    9.34   1216760            261            0         4.0            0.0   
4    9.67   1115468            223            0        13.5            1.0   

    likes  rating_participants  comments_count     감동/감탄  ...  genre_감성  \
0   91983               263859           82093  0.133333  ...     False   
1  134823               261048           56406  0.040000  ...     False   
2  355753               211459           32296  0.120000  ...     False   
3  373202               356731           41199  0.080000  ...     False   
4  265394               197599           17442  0.240000  ...     False   

   genre_개그  genre_드라마  genre_로맨스  genre_무협/사극  genre_스릴러  genre_스포츠  \
0     False      False      False        False      False      False   
1     False      False      False        False      False      False   
2     False      False       True        False      False      False   
3     False      False       True        False      False      False   
4     False      False      False        False      False      False   

   genre_액션  genre_일상  genre_판타지  
0     False     False       True  
1     False     False       True  
2     False     False      False  
3     False     False      False  
4      True     False      False  

[5 rows x 57 columns]

In [13]:
# episode_count 열을 int로 변환
data_cleaned['episode_count'] = data_cleaned['episode_count'].astype(int)

# work_count 열을 int로 변환 
data_cleaned['work_count'] = data_cleaned['work_count'].astype(int)

# previous_work 열을 int로 변환
data_cleaned['previous_work'] = data_cleaned['previous_work'].astype(int)

# originality 열을 0이면 False, 1이면 True로 변환
data_cleaned['originality'] = data_cleaned['originality'].apply(lambda x: True if x == 1 else False)

# 변환 결과 확인
data_cleaned.dtypes[0:20]

rating                 float64
interest                 int64
episode_count            int64
originality               bool
work_count               int64
previous_work            int64
likes                    int64
rating_participants      int64
comments_count           int64
감동/감탄                  float64
경악                     float64
고마움                    float64
공포/무서움                 float64
귀찮음                    float64
기대감                    float64
기쁨                     float64
깨달음                    float64
놀람                     float64
당황/난처                  float64
부담/안_내킴                float64
dtype: object

In [18]:
# 디바이스 설정
device = 1 if torch.cuda.is_available() else -1

# 데이터 준비 (target 열을 지정하세요)
target_column = "cluster"  # 정답 라벨링 열
features = data_cleaned.drop(columns=[target_column])
labels = data_cleaned[target_column]

# Train-Test Split (8:2 비율)
X_train, X_test, y_train, y_test = train_test_split(features, labels, test_size=0.2, random_state=17)

## 4-1.XGB

In [19]:
# 랜덤 서치 파라미터 설정
xgb_params = {
    "n_estimators": [100, 200],
    "learning_rate": [0.01, 0.1],
    "max_depth": [3, 5],
    "subsample": [0.8, 1.0],
    "colsample_bytree": [0.8, 1.0],
}

# XGBoost 모델 정의
xgb_model = XGBClassifier(use_label_encoder=False, eval_metric="logloss", random_state=17, tree_method="gpu_hist" if device == 1 else "auto")

# RandomizedSearchCV 설정
random_search_xgb = RandomizedSearchCV(
    estimator=xgb_model,
    param_distributions=xgb_params,
    n_iter=10,
    scoring="f1_macro",
    cv=3,
    verbose=2,
    n_jobs=-1,
    random_state=17
)

# 모델 학습
random_search_xgb.fit(X_train, y_train)

# 최적의 모델 및 파라미터 출력
print(f"Best Parameters for XGBoost: {random_search_xgb.best_params_}")
print(f"Best Cross-Validation F1 Macro for XGBoost: {random_search_xgb.best_score_:.4f}")

# 테스트 셋 성능 평가
best_xgb_model = random_search_xgb.best_estimator_
y_pred_xgb = best_xgb_model.predict(X_test)
print("Classification Report for XGBoost:\n")
print(classification_report(y_test, y_pred_xgb))

Fitting 3 folds for each of 32 candidates, totalling 96 fits


/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/sklearn/model_selection/_search.py:318: UserWarning: The total space of parameters 32 is smaller than n_iter=50. Running 32 iterations. For exhaustive searches, use GridSearchCV.
  warnings.warn(
/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:09:41] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:09:41] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, 

[CV] END colsample_bytree=0.8, learning_rate=0.01, max_depth=3, n_estimators=100, subsample=0.8; total time=  34.4s


/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:10:20] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:10:20] WARNING: /workspace/src/common/error_msg.cc:58: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device ordinal in the booster.
- Set the device for booster before call to inplace_predict.

This warning will only be shown once.

  warnings.warn(smsg, UserWarning)
/home/wanted-1/miniconda3/envs/project

[CV] END colsample_bytree=0.8, learning_rate=0.01, max_depth=3, n_estimators=100, subsample=1.0; total time=  38.6s


...

/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:13:19] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:13:19] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)


[CV] END colsample_bytree=1.0, learning_rate=0.1, max_depth=5, n_estimators=200, subsample=0.8; total time=  44.8s
[CV] END colsample_bytree=1.0, learning_rate=0.1, max_depth=5, n_estimators=200, subsample=1.0; total time=  43.3s


/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:13:20] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:13:20] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)


Best Parameters for XGBoost: {'subsample': 1.0, 'n_estimators': 200, 'max_depth': 3, 'learning_rate': 0.1, 'colsample_bytree': 0.8}
Best Cross-Validation F1 Macro for XGBoost: 0.8436
Classification Report for XGBoost:

              precision    recall  f1-score   support

         0.0       0.85      0.85      0.85        33
         1.0       0.78      0.50      0.61        14
         2.0       0.67      0.80      0.73        35
         3.0       0.83      0.83      0.83        52
         4.0       1.00      0.95      0.98        42
         5.0       1.00      1.00      1.00        31
         6.0       1.00      1.00      1.00        20
         7.0       1.00      1.00      1.00        15

    accuracy                           0.88       242
   macro avg       0.89      0.87      0.87       242
weighted avg       0.88      0.88      0.88       242



/home/wanted-1/miniconda3/envs/project2_team1/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [03:13:21] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)


In [28]:
import joblib

# 모델 저장
model_filename = "best_xgb_model.pkl"
joblib.dump(best_xgb_model, model_filename)

print(f" {model_filename} 저장 완료!")

# # 모델 로드
# loaded_model = joblib.load("best_xgb_model.pkl")

# # 로드된 모델로 예측 수행
# y_pred = loaded_model.predict(X_test)


 best_xgb_model.pkl 저장 완료!


## 4-2. catboost

NameError: name 'nvidia' is not defined

In [27]:
# 랜덤 서치 파라미터 설정
catboost_params = {
    "iterations": 500,
    "learning_rate": 0.1,
    "depth": 6,
    "task_type": "GPU",
    "max_ctr_complexity": 1,  # GPU 메모리 최적화
    "verbose": 100,
    "gpu_ram_part": 0.75,
    "devices": "1",  # 첫 번째 GPU 사용
}

# CatBoost 모델 정의
cat_model = CatBoostClassifier(verbose=0, random_state=17, task_type="GPU" if device == 1 else "CPU")

# RandomizedSearchCV 설정
random_search_cat = RandomizedSearchCV(
    estimator=cat_model,
    param_distributions=cat_params,
    n_iter=10,
    scoring="f1_macro",
    cv=3,
    verbose=2,
    n_jobs=-1,
    random_state=17,
)

# 모델 학습
random_search_cat.fit(X_train, y_train)

# 최적의 모델 및 파라미터 출력
print(f"Best Parameters for CatBoost: {random_search_cat.best_params_}")
print(f"Best Cross-Validation F1 Macro for CatBoost: {random_search_cat.best_score_:.4f}")

# 테스트 셋 성능 평가
best_cat_model = random_search_cat.best_estimator_
y_pred_cat = best_cat_model.predict(X_test)
print("Classification Report for CatBoost:\n")
print(classification_report(y_test, y_pred_cat))

Fitting 3 folds for each of 10 candidates, totalling 30 fits


uncaught exception:
    address -> 0x3b352450410
    what() -> "catboost/cuda/cuda_lib/cuda_base.cpp:16: CUDA error 2: out of memory"
    type -> TCatBoostException
uncaught exception:
    address -> 0x3f736450410
    what() -> "catboost/cuda/cuda_lib/cuda_base.cpp:16: CUDA error 2: out of memory"
    type -> TCatBoostException
uncaught exception:
    address -> 0x20b93850410
    what() -> "catboost/cuda/cuda_lib/cuda_base.cpp:16: CUDA error 2: out of memory"
    type -> TCatBoostException
uncaught exception:
    address -> 0x4dd82050410
uncaught exception:
    address -> 0x59378050410
    what() -> "catboost/cuda/cuda_lib/cuda_base.cpp:16: CUDA error 2: out of memory"
    what() -> "catboost/cuda/cuda_lib/cuda_base.cpp:16: CUDA error 2: out of memory"
    type -> TCatBoostException
    type -> TCatBoostException
uncaught exception:
    address -> 0x26229c50410
    what() -> "catboost/cuda/cuda_lib/cuda_base.cpp:16: CUDA error 2: out of memory"
uncaught exception:
    address -> 0x2823

TerminatedWorkerError: A worker process managed by the executor was unexpectedly terminated. This could be caused by a segmentation fault while calling the function or by an excessive memory usage causing the Operating System to kill the worker.

The exit codes of the workers are {SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6), SIGABRT(-6)}

## 4-3.LightGBM

In [21]:
# 랜덤 서치 파라미터 설정
lgbm_params = {
    "n_estimators": [100, 200, 300],
    "learning_rate": [0.01, 0.1, 0.2],
    "num_leaves": [31, 50, 100],
    "subsample": [0.6, 0.8, 1.0],
    "colsample_bytree": [0.6, 0.8, 1.0],
}

# LGBM 모델 정의
lgbm_model = LGBMClassifier(random_state=17, device="gpu" if device == 1 else "cpu")

# RandomizedSearchCV 설정
random_search_lgbm = RandomizedSearchCV(
    estimator=lgbm_model,
    param_distributions=lgbm_params,
    n_iter=10,
    scoring="f1_macro",
    cv=3,
    verbose=2,
    n_jobs=-1,
    random_state=17
)

# 모델 학습
random_search_lgbm.fit(X_train, y_train)

# 최적의 모델 및 파라미터 출력
print(f"Best Parameters for LGBM: {random_search_lgbm.best_params_}")
print(f"Best Cross-Validation F1 Macro for LGBM: {random_search_lgbm.best_score_:.4f}")

# 테스트 셋 성능 평가
best_lgbm_model = random_search_lgbm.best_estimator_
y_pred_lgbm = best_lgbm_model.predict(X_test)
print("Classification Report for LGBM:\n")
print(classification_report(y_test, y_pred_lgbm))

Fitting 3 folds for each of 10 candidates, totalling 30 fits
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 3363
[LightGBM] [Info] Number of data points in the train set: 643, number of used features: 47
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 3348
[LightGBM] [Info] Number of data points in the train set: 644, number of used features: 47
[LightGBM] [Info] Using GPU Device: NVIDIA GeForce RTX 4090, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 28 dense feature groups (0.02 MB) transferred to GPU in 0.003244 secs. 1 sparse feature groups
[LightGBM] [Info] Start training from score -2.000237
[LightGBM] [Info] Start training from score -2.828559
[LightGBM] [Info] Start training from score -1.721213
[LightGBM] [Info] Start training from score -1.560870
[LightGBM] [Info] Start train